## Whoosh bottle
### David O. Lignell

* Fill a bottle with a premixure of fuel and air.
* Light the top.
* The flame propagates down the bottle, with a jet and a *whoosh* out the top.
* Compute the exit velocity and estimate the pressure rise.
* Vary the ratio of the exit diamter to the bottle diameter.
* **Will it explode?**

**Code needs file [premixed_flame_speed.py](http://ignite.byu.edu/sharing/whoosh_bottle/premixed_flame_speed.py), and [streams.py](http://ignite.byu.edu/sharing/whoosh_bottle/streams.py), and also [etoh.xml](http://ignite.byu.edu/sharing/whoosh_bottle/etoh.xml)**

**You also need to have [Cantera](http://www.cantera.org/docs/sphinx/html/install.html) installed**

**The code below assumes pure ethanol as the fuel.**

In [9]:
from IPython.display import HTML
HTML('<iframe width="560" height="315" src="https://www.youtube.com/embed/tcrN5wMrS4w" frameborder="0" allow="autoplay; encrypted-media" allowfullscreen></iframe>')

In [2]:
import numpy             as np
import matplotlib.pyplot as plt
%matplotlib inline
import pint; u = pint.UnitRegistry()
import numpy as np
import streams
from premixed_flame_speed import premixed_flame_speed, suppress_stdout

In [3]:
def get_x_sat(Pa=85481, T=294):
    Psat = 1E5*10**(5.24677-1598.673/(T-46.424))  # etoh vapor pressure: Pa, 292-366 K. https://webbook.nist.gov/cgi/cbook.cgi?ID=C64175&Mask=4&Type=ANTOINE&Plot=on
    xF = Psat/Pa
    xO2 = (1-xF)*0.21
    xN2 = (1-xF)*0.79
    return {"c2h4oh":xF, "o2":xO2, "n2":xN2}

#-------------------------------

def get_x_spray_ϕ(nSpray, Vb=0.0246, Pa=85481, T=294):
    mEtOH = 0.11*nSpray/1000      # kg 
    nEtOH = mEtOH / 46.07         # kmol 
    nAir  = Pa*Vb / 8314.46 / T   # kmol
    ntot  = nEtOH + nAir
    xF = nEtOH / ntot
    xO2 = nAir * 0.21 / ntot
    xN2 = nAir * 0.79 / ntot
    #C2H6O +   3(O2 + 3.76N2) = 2CO2 + 3H2O + 3*3.76N2
    ϕ = (nEtOH/nAir) / (1/(3*4.76))
    return {"c2h4oh":xF, "o2":xO2, "n2":xN2}, ϕ

#-------------------------------

def get_x_vLiq(ϕ, Vb=0.0246, Pa=85481, T=294):
    ρ_EtOH = 790    # kg/m3
    nAir  = Pa*Vb / 8314.46 / T   # kmol
    nEtOH = nAir / (3*4.76) * ϕ   # kmol
    mEtOH = nEtOH * 46.07         # kg
    vEtOH = mEtOH/ρ_EtOH*100**3  # mm3
    ntot  = nEtOH + nAir
    xF = nEtOH / ntot
    xO2 = nAir * 0.21 / ntot
    xN2 = nAir * 0.79 / ntot
    return {"c2h4oh":xF, "o2":xO2, "n2":xN2}, vEtOH


In [5]:

Pa = 85481                  # atmospheric pressure (Pa)
Tr = 300                    # reactant temperature (K)
SL = 0.40                   # laminar flame speed  (m/s)
#------- 1 gallon bottle
#De = 1.0  /12/3.28084       # exit diameter        (m) 
#Db = 6.37 /12/3.28084       # bottle diameter      (m)
#H  = 12   /12/3.28084       # bottle height        (m)
#------- 6.5 gallon carboy bottle
De = 1.25  /12/3.28084      # exit diameter        (m) 
Db = 11.14 /12/3.28084      # bottle diameter      (m)
H  = 22    /12/3.28084      # bottle height        (m)  (22, 17)

#-----------------------------

s = streams.streams("o2:1,n2:3.76","c2h5oh:1", Tr, Tr, Pa, "etoh.xml")

ξ = s.get_ξ(get_x_sat(Pa, Tr), "mole")
x, ϕ = get_x_spray_ϕ(20)
#ϕ = 0.8
#x, vLiq = get_x_vLiq(ϕ)
#ξ = s.get_ξ(x, "mole")
print("ϕ =", ϕ)
#print("vLiq =", vLiq, " cm3")

s.set_gas_mixing_state(ξ)
ρr = s.gas.density           # reactant density (kg/m3)
with suppress_stdout():      # comment this line if you want to see the premix run output
    SL, Tp, ρp = premixed_flame_speed("etoh.xml", Tr, Pa, s.gas.X);

#-----------------------------

Ae = np.pi/4*De**2          # exit cross sectional area (m2)
Ab = np.pi/4*Db**2          # bottle cross sectional area (m2)

mdot = ρr * Ab * SL         # mass burning rate (kg/s)
vb   = mdot / ρp / Ab       # velocity in the bottle (m/s) (products)
ve   = mdot / ρp / Ae       # gas velocity at the exit

#-----------------------------

Pb = Pa + ρp*(ve**2 - vb**2)/2   # Bernoulli Equation bottle pressure (Pa)

#-----------------------------

print("exit gas temperature     = {:4.0f} K  ".format(Tp))
print("exit velocity            = {:4.1f} m/s".format(ve))
print("product vel in bottle    = {:4.3f} m/s".format(vb))
print("advancing flame speed    = {:4.3f} m/s".format(SL))
print("bottle pressure (gage)   = {:4.3f} psi".format((Pb-Pa)*14.695948/101325))
print("bottle P / atmospheric P = {:4.3f}    ".format(Pb/Pa))
print("burn time                = {:4.3f} s  ".format(H/SL))
print("Pstatic water ρw*g*H     = {:4.3f} psi".format(1000*9.81*H/101325*14.695948))

ϕ = 0.792700904077629
exit gas temperature     = 1955 K  
exit velocity            = 109.6 m/s
product vel in bottle    = 1.381 m/s
advancing flame speed    = 0.178 m/s
bottle pressure (gage)   = 0.117 psi
bottle P / atmospheric P = 1.009    
burn time                = 3.145 s  
Pstatic water ρw*g*H     = 0.795 psi
